In [1]:
import pandas as pd
import numpy as np
import math
from datetime import datetime
import csv
import time



# Loading original dataset

In [2]:
dataset = pd.read_csv('data4.csv', delimiter=";")

C:\Users\silva\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3146: DtypeWarning: Columns (7) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


# selecting sensor dataset 

In [3]:
nset  = dataset[(dataset["moteid"] ==3)]
nset

date             time  epoch  moteid  temperature  humidity  \
89962   31/03/2004  02:58:45.763421      2       3      122.153  -391.901   
89963   28/02/2004  00:58:46.497331      2       3       20.204   368.871   
89964   30/03/2004  16:04:46.552435      3       3      122.153  -391.901   
89965   30/03/2004  14:43:05.262873      4       3      122.153  -391.901   
89966   30/03/2004  16:06:06.095868      5       3      122.153  -391.901   
...            ...              ...    ...     ...          ...       ...   
136591  21/03/2004  19:03:27.962292  65530       3      211.938    47.212   
136592  21/03/2004  19:04:05.864445  65531       3       21.184   470.486   
136593  21/03/2004  19:04:39.951966  65532       3      211.938   469.505   
136594  21/03/2004  19:05:14.205856  65533       3       21.184   468.524   
136595  21/03/2004  19:05:40.003996  65534       3       21.184   468.524   

         light  voltage  Unnamed: 8  
89962    19.32  208.393         NaN  
89963    50.60  269.964         NaN  
89964   235.52  212.875         NaN  
89965   397.44   21.364         NaN  
89966   235.52   21.364         NaN  
...        ...      ...         ...  
136591    2.30  238.522         NaN  
136592    2.30  238.522         NaN  
136593    1.84  238.522         NaN  
136594    1.84  238.522         NaN  
136595    1.84  238.522         NaN  

[46634 rows x 9 columns]

In [4]:
nset.date = nset.date+ ' ' +nset.time

C:\Users\silva\anaconda3\lib\site-packages\pandas\core\generic.py:5168: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value


In [5]:
print(nset.date.shape[0])

46634


# build timestamp

In [6]:

#removing local from time
for i in np.arange(nset['date'].shape[0]):
    x = nset.date.iloc[i].split('.')
    nset.date.iloc[i] = x[0]
    


C:\Users\silva\anaconda3\lib\site-packages\pandas\core\indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)
<ipython-input-6-53520b216154>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nset.date.iloc[i] = x[0]


In [7]:
nset.date= pd.to_datetime(nset.date, infer_datetime_format=True)

# drop unused columns

In [8]:
nset.drop('time', axis=1, inplace=True)

C:\Users\silva\anaconda3\lib\site-packages\pandas\core\frame.py:4163: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


# build ML dataset part 1

In [9]:
MyLIst = []

for i in np.arange((nset.shape[0]-1)):
        dalay = (nset.iloc[i+1, 0] - nset.iloc[i, 0]).total_seconds()
        delta_temperature = abs(nset.iloc[i+1, 3] - nset.iloc[i, 3])
        sensor_id = nset.iloc[i,2]
        hour = nset.iloc[i, 0].hour
        minute = nset.iloc[i, 0].minute
        second = nset.iloc[i, 0].second
        day = nset.iloc[i, 0].day
        month = nset.iloc[i, 0].month
        label = 0
        if(delta_temperature>=3):
            label=1
        MyLIst.append([nset.iloc[i, 0], hour,minute,second,day,month, dalay, sensor_id, nset.iloc[i, 3], label])
    


In [10]:
cols = ['timestamp', 'hour','minut','second','day','month', 'delay', 'sensor_id', 'temperature','label']
df_ML = pd.DataFrame(MyLIst, columns = cols)


# updating label and dalay to concept drift

In [11]:
def create_window(X, time_steps=50):
    Xs = []
    for i in range(len(X) - time_steps):
        v = X.iloc[i: (i+time_steps), 8].to_numpy()
        Xs.append(v)
    return np.array(Xs)

In [12]:
df_ML.iloc[:,8].mean()

177.51622664206852

In [13]:
WINDOW = 50
data_stream = create_window(df_ML, time_steps=WINDOW)


In [14]:
data_stream.shape[0]

46583

In [15]:
# Imports
import numpy as np
from skmultiflow.drift_detection import PageHinkley
ph = PageHinkley()

# Adding stream elements to the PageHinkley drift detector and verifying if drift occurred

for i in np.arange(data_stream.shape[0]):  
    CHANGE = 0
    DELAY= 0
    for j in np.arange(data_stream[i].shape[0]):  
        ph.add_element(data_stream[i][j])
        if ph.detected_change():
            CHANGE = 1
            print('Change has been detected in data: ' + str(data_stream[i][j]) + ' - delay: '+str(DELAY) +' - of index: '+str(i)+'x'+str(i) )
    init = i*WINDOW    
    df_ML.iloc[init: (init+WINDOW), 9] = CHANGE
    df_ML.iloc[init: (init+WINDOW), 6] =  dalay
    DELAY +=200000
    if(CHANGE):
        CHANGE = 0
        DELAY= 0 
        
    

Change has been detected in data: 193.514 - delay: 0 - of index: 0x0
Change has been detected in data: 122.15299999999999 - delay: 0 - of index: 1x1
Change has been detected in data: 193.024 - delay: 0 - of index: 1x1
Change has been detected in data: 193.612 - delay: 0 - of index: 2x2
Change has been detected in data: 191.554 - delay: 0 - of index: 2x2
Change has been detected in data: 193.31799999999998 - delay: 0 - of index: 3x3
Change has been detected in data: 122.15299999999999 - delay: 0 - of index: 4x4
Change has been detected in data: 193.024 - delay: 0 - of index: 4x4
Change has been detected in data: 193.612 - delay: 0 - of index: 5x5
Change has been detected in data: 191.554 - delay: 0 - of index: 5x5
Change has been detected in data: 193.31799999999998 - delay: 0 - of index: 6x6
Change has been detected in data: 122.15299999999999 - delay: 0 - of index: 7x7
Change has been detected in data: 193.024 - delay: 0 - of index: 7x7
Change has been detected in data: 193.612 - dela

Change has been detected in data: 19.028 - delay: 0 - of index: 102x102
Change has been detected in data: 18.783 - delay: 0 - of index: 102x102
Change has been detected in data: 189.49599999999998 - delay: 0 - of index: 103x103
Change has been detected in data: 188.02599999999998 - delay: 0 - of index: 103x103
Change has been detected in data: 189.104 - delay: 0 - of index: 104x104
Change has been detected in data: 187.144 - delay: 0 - of index: 104x104
Change has been detected in data: 188.12400000000002 - delay: 0 - of index: 105x105
Change has been detected in data: 18.979 - delay: 0 - of index: 106x106
Change has been detected in data: 188.12400000000002 - delay: 0 - of index: 106x106
Change has been detected in data: 189.202 - delay: 0 - of index: 107x107
Change has been detected in data: 18.685 - delay: 0 - of index: 107x107
Change has been detected in data: 188.12400000000002 - delay: 0 - of index: 108x108
Change has been detected in data: 18.979 - delay: 0 - of index: 109x109
C

Change has been detected in data: 184.204 - delay: 0 - of index: 206x206
Change has been detected in data: 182.048 - delay: 0 - of index: 206x206
Change has been detected in data: 184.00799999999998 - delay: 0 - of index: 207x207
Change has been detected in data: 181.852 - delay: 0 - of index: 207x207
Change has been detected in data: 183.028 - delay: 0 - of index: 208x208
Change has been detected in data: 184.204 - delay: 0 - of index: 209x209
Change has been detected in data: 182.048 - delay: 0 - of index: 209x209
Change has been detected in data: 184.00799999999998 - delay: 0 - of index: 210x210
Change has been detected in data: 181.852 - delay: 0 - of index: 210x210
Change has been detected in data: 183.028 - delay: 0 - of index: 211x211
Change has been detected in data: 184.204 - delay: 0 - of index: 212x212
Change has been detected in data: 182.048 - delay: 0 - of index: 212x212
Change has been detected in data: 184.00799999999998 - delay: 0 - of index: 213x213
Change has been de

Change has been detected in data: 177.638 - delay: 0 - of index: 313x313
Change has been detected in data: 17.852 - delay: 0 - of index: 314x314
Change has been detected in data: 177.34400000000002 - delay: 0 - of index: 314x314
Change has been detected in data: 178.128 - delay: 0 - of index: 315x315
Change has been detected in data: 177.442 - delay: 0 - of index: 315x315
Change has been detected in data: 177.638 - delay: 0 - of index: 316x316
Change has been detected in data: 17.852 - delay: 0 - of index: 317x317
Change has been detected in data: 177.34400000000002 - delay: 0 - of index: 317x317
Change has been detected in data: 178.128 - delay: 0 - of index: 318x318
Change has been detected in data: 177.442 - delay: 0 - of index: 318x318
Change has been detected in data: 177.638 - delay: 0 - of index: 319x319
Change has been detected in data: 17.852 - delay: 0 - of index: 320x320
Change has been detected in data: 177.34400000000002 - delay: 0 - of index: 320x320
Change has been detec

Change has been detected in data: 184.69400000000002 - delay: 0 - of index: 417x417
Change has been detected in data: 180.088 - delay: 0 - of index: 418x418
Change has been detected in data: 186.16400000000002 - delay: 0 - of index: 418x418
Change has been detected in data: 183.22400000000002 - delay: 0 - of index: 419x419
Change has been detected in data: 187.928 - delay: 0 - of index: 419x419
Change has been detected in data: 184.69400000000002 - delay: 0 - of index: 420x420
Change has been detected in data: 179.696 - delay: 0 - of index: 421x421
Change has been detected in data: 186.16400000000002 - delay: 0 - of index: 421x421
Change has been detected in data: 183.322 - delay: 0 - of index: 422x422
Change has been detected in data: 18.832 - delay: 0 - of index: 422x422
Change has been detected in data: 184.792 - delay: 0 - of index: 423x423
Change has been detected in data: 179.696 - delay: 0 - of index: 424x424
Change has been detected in data: 186.16400000000002 - delay: 0 - of i

...

Change has been detected in data: 241.142 - delay: 0 - of index: 46177x46177
Change has been detected in data: 240.65200000000002 - delay: 0 - of index: 46178x46178
Change has been detected in data: 242.416 - delay: 0 - of index: 46178x46178
Change has been detected in data: 241.632 - delay: 0 - of index: 46179x46179
Change has been detected in data: 244.082 - delay: 0 - of index: 46179x46179
Change has been detected in data: 241.142 - delay: 0 - of index: 46180x46180
Change has been detected in data: 240.65200000000002 - delay: 0 - of index: 46181x46181
Change has been detected in data: 242.416 - delay: 0 - of index: 46181x46181
Change has been detected in data: 241.632 - delay: 0 - of index: 46182x46182
Change has been detected in data: 244.082 - delay: 0 - of index: 46182x46182
Change has been detected in data: 241.142 - delay: 0 - of index: 46183x46183
Change has been detected in data: 240.65200000000002 - delay: 0 - of index: 46184x46184
Change has been detected in data: 242.416 -

Change has been detected in data: 24.516 - delay: 0 - of index: 46280x46280
Change has been detected in data: 240.358 - delay: 0 - of index: 46280x46280
Change has been detected in data: 242.514 - delay: 0 - of index: 46281x46281
Change has been detected in data: 245.356 - delay: 0 - of index: 46282x46282
Change has been detected in data: 241.43599999999998 - delay: 0 - of index: 46282x46282
Change has been detected in data: 24.516 - delay: 0 - of index: 46283x46283
Change has been detected in data: 240.358 - delay: 0 - of index: 46283x46283
Change has been detected in data: 242.514 - delay: 0 - of index: 46284x46284
Change has been detected in data: 245.356 - delay: 0 - of index: 46285x46285
Change has been detected in data: 241.43599999999998 - delay: 0 - of index: 46285x46285
Change has been detected in data: 24.516 - delay: 0 - of index: 46286x46286
Change has been detected in data: 240.358 - delay: 0 - of index: 46286x46286
Change has been detected in data: 242.514 - delay: 0 - of

Change has been detected in data: 230.06799999999998 - delay: 0 - of index: 46375x46375
Change has been detected in data: 232.12599999999998 - delay: 0 - of index: 46376x46376
Change has been detected in data: 229.676 - delay: 0 - of index: 46376x46376
Change has been detected in data: 230.65599999999998 - delay: 0 - of index: 46377x46377
Change has been detected in data: 229.088 - delay: 0 - of index: 46377x46377
Change has been detected in data: 230.06799999999998 - delay: 0 - of index: 46378x46378
Change has been detected in data: 232.12599999999998 - delay: 0 - of index: 46379x46379
Change has been detected in data: 229.676 - delay: 0 - of index: 46379x46379
Change has been detected in data: 230.65599999999998 - delay: 0 - of index: 46380x46380
Change has been detected in data: 229.088 - delay: 0 - of index: 46380x46380
Change has been detected in data: 230.06799999999998 - delay: 0 - of index: 46381x46381
Change has been detected in data: 228.892 - delay: 0 - of index: 46381x46381

Change has been detected in data: 223.796 - delay: 0 - of index: 46468x46468
Change has been detected in data: 222.032 - delay: 0 - of index: 46468x46468
Change has been detected in data: 222.81599999999997 - delay: 0 - of index: 46469x46469
Change has been detected in data: 221.248 - delay: 0 - of index: 46469x46469
Change has been detected in data: 22.311 - delay: 0 - of index: 46470x46470
Change has been detected in data: 224.188 - delay: 0 - of index: 46471x46471
Change has been detected in data: 222.326 - delay: 0 - of index: 46471x46471
Change has been detected in data: 22.311 - delay: 0 - of index: 46472x46472
Change has been detected in data: 221.542 - delay: 0 - of index: 46472x46472
Change has been detected in data: 223.208 - delay: 0 - of index: 46473x46473
Change has been detected in data: 224.77599999999998 - delay: 0 - of index: 46474x46474
Change has been detected in data: 222.424 - delay: 0 - of index: 46474x46474
Change has been detected in data: 22.311 - delay: 0 - of

Change has been detected in data: 214.192 - delay: 0 - of index: 46570x46570
Change has been detected in data: 215.56400000000002 - delay: 0 - of index: 46571x46571
Change has been detected in data: 213.50599999999997 - delay: 0 - of index: 46571x46571
Change has been detected in data: 214.878 - delay: 0 - of index: 46572x46572
Change has been detected in data: 212.722 - delay: 0 - of index: 46572x46572
Change has been detected in data: 214.192 - delay: 0 - of index: 46573x46573
Change has been detected in data: 212.722 - delay: 0 - of index: 46573x46573
Change has been detected in data: 213.50599999999997 - delay: 0 - of index: 46574x46574
Change has been detected in data: 214.878 - delay: 0 - of index: 46575x46575
Change has been detected in data: 212.722 - delay: 0 - of index: 46575x46575
Change has been detected in data: 214.192 - delay: 0 - of index: 46576x46576
Change has been detected in data: 212.722 - delay: 0 - of index: 46576x46576
Change has been detected in data: 213.50599

# Registring ML in csv

In [16]:
df_ML

timestamp  hour  minut  second  day  month  delay  sensor_id  \
0     2004-03-31 02:58:45     2     58      45   31      3   26.0          3   
1     2004-02-28 00:58:46     0     58      46   28      2   26.0          3   
2     2004-03-30 16:04:46    16      4      46   30      3   26.0          3   
3     2004-03-30 14:43:05    14     43       5   30      3   26.0          3   
4     2004-03-30 16:06:06    16      6       6   30      3   26.0          3   
...                   ...   ...    ...     ...  ...    ...    ...        ...   
46628 2004-03-21 19:02:56    19      2      56   21      3   26.0          3   
46629 2004-03-21 19:03:27    19      3      27   21      3   26.0          3   
46630 2004-03-21 19:04:05    19      4       5   21      3   26.0          3   
46631 2004-03-21 19:04:39    19      4      39   21      3   26.0          3   
46632 2004-03-21 19:05:14    19      5      14   21      3   26.0          3   

       temperature  label  
0          122.153      1  
1           20.204      1  
2          122.153      1  
3          122.153      1  
4          122.153      1  
...            ...    ...  
46628      212.134      1  
46629      211.938      1  
46630       21.184      1  
46631      211.938      1  
46632       21.184      1  

[46633 rows x 10 columns]

In [17]:
f = open('sdn_ml.csv','w')
try:
    writer = csv.writer(f)
    writer.writerow(df_ML.columns)
    for i in np.arange(int(df_ML.shape[0])):
        writer.writerow(df_ML.iloc[i,])
finally:
    f.close()